<a href="https://colab.research.google.com/github/Jorbnc/MAIA-RL/blob/master/RL_proyecto_Primera_Entrega.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Tareas

* Guardar copia de repositorio en GitHub y limpiar lo que no es de la 1ra entrega

* Dejar más claro en el PDF los estados "terminales"

*  Ajustar el nombre de las variables en la visualización

* Trabajar en el gif del notebook

# Importaciones

In [96]:
# Para anotar los tipos de argumentos del tablero
from typing import Tuple, List

# Para toma de decisiones
import random
import numpy as np

# Tiempo de Aprendizaje
import time

# Para visualización
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import matplotlib.animation as animation

from matplotlib.textpath import TextPath
from matplotlib.markers  import MarkerStyle
from matplotlib.path     import Path
from matplotlib.transforms import Affine2D
from matplotlib.patches  import PathPatch, FancyArrowPatch
from matplotlib import rc
import matplotlib.animation as animation
from IPython.display import display

np.random.seed(13)
%matplotlib notebook

# Tablero

In [17]:
#Validar que el número de celda esté dentro de los límites del tablero
def limites_validos(celda, celda_max) -> bool:
    return 1 <= celda <= celda_max

# Definición del ambiente
class Tablero:
    def __init__(
        self,
        nro_filas: int,
        nro_columnas: int,
        celda_victoria: int,
        celdas_perdida: List[int],
        celdas_escalera: List[Tuple[int]],
        celdas_rodadero: List[Tuple[int]],
    ):
        # ----------------------------------------------------------------------
        # Validación de condiciones mínimas para el tablero
        if nro_filas < 2 or nro_columnas < 2:
            raise ValueError("Debe haber al menos 2 filas y 2 columnas")
        # N= Filas x Columnas representa el número total de casillas del tablero
        self.celda_max = nro_filas * nro_columnas
        celdas_a_validar = ([celda_victoria] + celdas_perdida
                            + [celda for par in celdas_escalera for celda in par]
                            + [celda for par in celdas_rodadero for celda in par]
                            )
        # Validamos las ubicaciones o estados dados por parámetros sean válidos
        for celda in celdas_a_validar:
            if not limites_validos(celda, self.celda_max):
                raise ValueError(f"{celda} fuera de los limites: {1} a {self.celda_max}")

        # Una celda de pérdida no puede ser una celda de victoria
        for c in celdas_perdida:
            if c == celda_victoria:
                raise ValueError(f"Estado de pérdida {c} debe ser diferente a estado de victoria {celda_victoria}")

        # ----------------------------------------------------------------------
        # Definición de Atributos
        self.nro_filas = nro_filas
        self.nro_columnas = nro_columnas
        self.celda_victoria = celda_victoria
        self.celdas_perdida = celdas_perdida
        self.celdas_escalera = celdas_escalera
        self.celdas_rodadero = celdas_rodadero

        # Mismo diccionario para las transiciones de las escaleras y de los rodaderos
        self.escaleras_y_rodaderos = {**dict(celdas_escalera), **dict(celdas_rodadero)}

        # Definición de la recompensa para: ganar o perder el juego
        self.reward_map = {
            self.celda_victoria: 1.0,
            **{cell: -1.0 for cell in self.celdas_perdida}
        }

    #Representación impresa del Tablero
    def __repr__(self) -> str:

        atributos = [
            ("Número de filas", self.nro_filas),
            ("Número de columnas", self.nro_columnas),
            ("Celda máxima", self.celda_max),
            ("Celda victoria", self.celda_victoria),
            ("Celdas perdida", self.celdas_perdida),
            ("Celdas escalera", self.celdas_escalera),
            ("Celdas rodadero", self.celdas_rodadero),
        ]
        atributos_str = "\n".join(f" {nombre}: {valor}" for nombre, valor in atributos)
        return f"Tablero:\n{atributos_str}\n"

    # Obtener coordenada (columna, fila) a partir del número de celda y el número de columnas
    def celda_a_coord(self, nro_celda) -> tuple[int, int]:

        # -1 para manejar los multiplos de 'nro_columnas'
        fila = ((nro_celda - 1) // self.nro_columnas) + 1
        offset = (nro_celda - 1) % self.nro_columnas

        # Fila impar
        if fila % 2 == 1:
            # Izquierda a derecha
            columna = offset + 1
        else:
            # Derecha a izquierda
            columna = self.nro_columnas - offset
        # Centrar
        return (columna - 0.5, fila - 0.5)

    #Obtener el número de celda a partir del par: (columna, fila)
    def coord_a_celda(self, col, fila) -> int:

        valor_inicial = (fila - (fila % 2)) * self.nro_columnas
        offset = (-1) ** (fila - 1) * (col - ((fila - 1) % 2))
        return valor_inicial + offset

    # Saber si el estado es terminal
    def is_terminal(self, estado) -> bool:
        return estado == self.celda_victoria or estado in self.celdas_perdida

# Para exportar/importar con `from Tablero import`
__all__ = ["limites_validos", "Tablero"]

# Agente

In [18]:
class AgenteQLearning: # Sugiero cambiar nombre para la primera entrega
    def __init__(self, tablero: Tablero, alpha: float = 0.1, gamma: float = 0.9, epsilon: float = 0.1):

        # Ambiente
        self.tablero = tablero

        # Parámetros del agente (algunos parámetros podrían ajustarse en la entrega final, por ahora se usan parámetros escogidos al azar)
        # Tasa de aprendizaje
        self.alpha = alpha
        # Factor de descuento
        self.gamma = gamma
        # Ratio de exploración
        self.epsilon = epsilon
        # Posición inicial siempre en 1
        self.pos = 1
        # Izquierda/Derecha o Avanzar/ Retroceder
        self.acciones = [-1, 1]

        # Q-table (o Q-dict en nuestro caso)
        self.Q = {}  # No va entrega parcial

    #Escoge una acción
    def escoger_accion(self, estado) -> int:

        # Desde acá....
        # Exploración
        if random.random() < self.epsilon:
            return random.choice(self.acciones)

        # Explotación
        else:
            # Obtener los mejores valores Q (0 en caso aún no exista)
            Q_vals = [self.Q.get((estado, a), 0.0) for a in self.acciones]
            Q_max = max(Q_vals)

            # En caso de empate, escoger aleatoriamente una acción
            mejores_acciones = [a for a, Q in zip(self.acciones, Q_vals) if Q == Q_max]
            return random.choice(mejores_acciones)
          # Hasta acá no iría en la entrega parcial

        # Iría en la entrega parcial:
        # if self.tablero.is_terminal(estado):
        #   return None
        # else:
        #   return random.choice(self.acciones)


    # Desde acá....
    def actualizar_Q(self, estado, accion, reward, estado_siguiente) -> None:
        """
        Actualización Q-learning con base en(Sₜ,Aₜ,Rₜ,Sₜ₊₁):
            Q(Sₜ,Aₜ) = Q(Sₜ,Aₜ) + α[Rₜ₊₁ + γ*maxₐ Q(Sₜ₊₁,a) - Q(Sₜ,Aₜ)]    (Sutton & Barto, p. 131)
        """
        Q_actual = self.Q.get((estado, accion), 0.0)

        # Estimar mejor Q en el siguiente estado
        Q_vals_siguiente_max = max([self.Q.get((estado_siguiente, a), 0.0) for a in self.acciones])

        # Actualización
        # TODO: Probar si hay cambios importantes al variar gamma
        self.Q[(estado, accion)] = Q_actual + self.alpha * (reward + self.gamma * Q_vals_siguiente_max - Q_actual)
    # Hasta acá no iría en la entrega parcial

    #Definición de función de transición
    def transicion(self, estado, accion):
        if accion != None:
          estado_siguiente = estado + accion

          estado_siguiente = self.tablero.escaleras_y_rodaderos.get(
              # Si el estado_siguiente es el inicio de una escalera/rodadero, entonces retorna el final
              estado_siguiente,
              # En caso contrario, solo valida el estado_siguiente
              max(1, min(estado_siguiente, self.tablero.celda_max))
          )
          # Aclaración: No se evalua condición de terminación. Esto será manejado la fase de simulación
          return estado_siguiente
        else:
          return estado

    #Función de recompensa basado en un mapeo (diccionario): Sₜ₊₁ -> reward
    def reward(self, estado_siguiente):
        return self.tablero.reward_map.get(estado_siguiente, 0)


    #Representa un paso en la simulación con base en las condiciones actuales.
    #Actualiza la Q-table con base en (Sₜ,Aₜ,Rₜ,Sₜ₊₁) y retorna la tupla. # No va entrega parcial

    def step(self) -> Tuple[int, int, float, int]:
        estado = self.pos
        accion = self.escoger_accion(estado)

        # Transición y Reward del paso actual
        estado_siguiente = self.transicion(estado, accion)
        reward = self.reward(estado_siguiente)

        # Actualizar Q y estado (pos) # No va entrega parcial
        self.actualizar_Q(estado, accion, reward, estado_siguiente) # No va entrega parcial
        self.pos = estado_siguiente

        return estado, accion, reward, estado_siguiente

# Visualización

In [97]:
# Configuración de símbolos
_AGENT_CHAR = "\u263A"
_SKULL_CHAR = "\u2620"

# Convierte un carácter Unicode en un MarkerStyle centrado
def _marker_from_char(char: str, size: float = 1):

    tp = TextPath((0, 0), char, size=size)
    bbox = tp.get_extents()
    # Centramos el glifo para que el marcador quede alineado
    tp = tp.transformed(
        Affine2D().translate(
            -(bbox.x0 + bbox.width / 2),
            -(bbox.y0 + bbox.height / 2),
        )
    )
    return MarkerStyle(tp)

# Marcadores listos para usar
_SKULL_MK = _marker_from_char(_SKULL_CHAR)
_AGENT_MK = _marker_from_char(_AGENT_CHAR)

# Curvas y utilidades geométricas
#Devuelve n-1 vectores unitarios equiespaciados entre los puntos u y v
def _vector(u, v, n):

    return np.diff(np.linspace(u, v, n), axis=0)

#Devuelve un Path que conecta u y v con una curva "Bézier" suavemente aleatorizada
def _rand_curve(u, v, amp=2.85, n_sub=120):

    u, v = np.asarray(u), np.asarray(v)
    dv = v - u
    perp = np.array([-dv[1], dv[0]]) / np.linalg.norm(dv)

    ctrl1 = u + 0.3 * dv + perp * amp * np.random.uniform(-1, 1)
    ctrl2 = u + 0.7 * dv - perp * amp * np.random.uniform(-1, 1)

    bez = Path([u, ctrl1, ctrl2, v],
               [Path.MOVETO, Path.CURVE4, Path.CURVE4, Path.CURVE4])

    t = np.linspace(0, 1, n_sub)
    B = lambda p0, p1, p2, p3, t: (
        (1 - t) ** 3 * p0 + 3 * (1 - t) ** 2 * t * p1
        + 3 * (1 - t) * t ** 2 * p2 + t ** 3 * p3
    )
    verts = np.column_stack((B(*bez.vertices[:, 0], t), B(*bez.vertices[:, 1], t)))
    codes = [Path.MOVETO] + [Path.LINETO] * (len(verts) - 1)
    return Path(verts, codes)


# Dibujo de escaleras y rodaderos
#Dibuja una escalera entre u y v
def dibujar_escalera(ax, u, v, *, color="#2ecc71", rungs=6, width=6, rung_ratio=0.20, shadow_offset=(0.03, -0.03)):

    sombra = PathPatch(Path([u, v], [Path.MOVETO, Path.LINETO]), lw=width,
                       edgecolor="k", alpha=0.08, capstyle="round", zorder=1,
                       transform=Affine2D().translate(*shadow_offset) + ax.transData)
    ax.add_patch(sombra)

    ax.plot([u[0], v[0]], [u[1], v[1]], lw=width, color=color, solid_capstyle="round", zorder=2)

    u, v = np.asarray(u), np.asarray(v)
    interp = np.linspace(u, v, rungs + 2)[1:-1]
    ortho = np.array([v[1] - u[1], -(v[0] - u[0])])
    ortho = ortho / np.linalg.norm(ortho) * rung_ratio * np.linalg.norm(v - u) / rungs

    for p in interp:
        p1, p2 = p - ortho, p + ortho
        ax.plot([p1[0] + shadow_offset[0], p2[0] + shadow_offset[0]],
                [p1[1] + shadow_offset[1], p2[1] + shadow_offset[1]], lw=width,
                color="k", alpha=0.08, solid_capstyle="round", zorder=1)
        ax.plot([p1[0], p2[0]], [p1[1], p2[1]], lw=width, color=color, solid_capstyle="round", zorder=2)

#  Dibuja un rodadero curvo con sombra y flecha
def dibujar_rodadero(ax, u, v, *, color="#e74c3c"):

    path = _rand_curve(u, v, amp=0.5, n_sub=120)

    ax.add_patch(PathPatch(path, lw=6, edgecolor="k", alpha=0.08, zorder=1,
                            transform=Affine2D().translate(0.03, -0.03) + ax.transData))
    ax.add_patch(PathPatch(path, lw=6, edgecolor=color, facecolor="none", capstyle="round", zorder=2))
    ax.add_patch(FancyArrowPatch(path.vertices[-2], path.vertices[-1], arrowstyle="simple",
                                 mutation_scale=16, color=color, lw=0, zorder=3))


# Plot principal del tablero
# Despliega el tablero y anima la trayectoria del agente si se provee
def plot_tablero(tablero, trayectoria=None):


    n_rows, n_cols = tablero.nro_filas, tablero.nro_columnas
    fig, ax = plt.subplots(figsize=(n_cols, n_rows), dpi=75)

    ax.set(xlim=(0, n_cols), ylim=(0, n_rows))
    ax.set_xticks(range(1, n_cols + 1))
    ax.set_yticks(range(1, n_rows + 1))
    ax.grid(color="black", linewidth=1)
    ax.tick_params(axis="both", which="both", labelbottom=False, labelleft=False,
                   bottom=False, left=False, top=False, right=False)

    # Numeración de celdas
    for fila in range(1, n_rows + 1):
        for col in range(1, n_cols + 1):
            ax.text(col - 0.5, fila - 0.35, str(tablero.coord_a_celda(col, fila)),
                    ha="center", va="bottom", alpha=0.5)

    # Casilla de victoria
    ax.text(*tablero.celda_a_coord(tablero.celda_victoria), "FIN", ha="center", va="top", color="green", size=15)

    # Calaveras
    for c in tablero.celdas_perdida:
        ax.scatter(*tablero.celda_a_coord(c), marker=_SKULL_MK, s=3500, color="red", zorder=5)

    # Escaleras y rodaderos
    for a, b in tablero.celdas_escalera:
        dibujar_escalera(ax, tablero.celda_a_coord(a), tablero.celda_a_coord(b))
    for a, b in tablero.celdas_rodadero:
        dibujar_rodadero(ax, tablero.celda_a_coord(a), tablero.celda_a_coord(b))

    # Animación de la trayectoria
    if trayectoria:
        agent = ax.scatter([], [], marker=_AGENT_MK, s=2500, color="blue", zorder=6)

        def _update(frame):
            agent.set_offsets([tablero.celda_a_coord(trayectoria[frame])])
            return (agent,)

        animation.FuncAnimation(fig, _update, frames=len(trayectoria), interval=200, repeat=True, blit=True)

    plt.show()

# Simulación

In [98]:
# Correr simulación y plotear la última trayectoria
def run(tablero, agente,
        episodios=1000,
        mostrar_inline=True,
        guardar_gif=False,
        gif_name='trayectoria.gif',
        fps=5):
    """
    Ejecuta `episodios` de entrenamiento y anima la trayectoria del último.

    Parámetros
    ----------
    mostrar_inline : bool
        Muestra el reproductor HTML5 en Colab/Jupyter al finalizar.
    guardar_gif : bool
        Guarda la animación como GIF con Pillow.
    gif_name : str
        Nombre del archivo GIF de salida.
    fps : int
        Cuadros por segundo del GIF (solo si guardar_gif=True).
    """
    reward_acumulado = []
    ultima_trayectoria = None

    # ───── Entrenamiento ───────────────────────────────────────────────────
    for episodio in range(episodios):
        agente.pos = 1
        trayectoria = [agente.pos]
        pasos = 0

        while True:
            estado, accion, reward, estado_siguiente = agente.step()
            pasos += 1
            trayectoria.append(estado_siguiente)
            reward_acumulado.append(reward)

            # Condición de finalización
            if tablero.is_terminal(estado_siguiente):
                print(f"Episodio {episodio + 1} terminó en {pasos} pasos, "
                      f"reward {reward}.")
                break                       # sale del while

        # Conservar la trayectoria más reciente
        ultima_trayectoria = trayectoria

    # ───── Visualización ──────────────────────────────────────────────────
    plot_tablero(tablero)                   # dibuja el tablero (sin animar)
    fig = plt.gcf()
    ax  = plt.gca()

    # Agente (carita ☺) – usa el marcador definido en tu módulo
    agent_scatter = ax.scatter([], [], marker=_AGENT_MK,
                               s=2500, color='blue', zorder=6)

    def _update(frame):
        # Mueve la carita a la celda correspondiente
        agent_scatter.set_offsets([tablero.celda_a_coord(
            ultima_trayectoria[frame])])
        return (agent_scatter,)

    anim = animation.FuncAnimation(
        fig, _update,
        frames=len(ultima_trayectoria),
        interval=200,          # 200 ms -> 5 fps
        repeat=True,
        blit=True
    )

    # Mostrar inline (HTML5)
    if mostrar_inline:
        rc('animation', html='jshtml')
        display(anim)

    # Guardar GIF
    if guardar_gif:
        anim.save(gif_name, writer='pillow', fps=fps)
        print(f'GIF guardado en {gif_name}')

    return anim

# Main

In [99]:
# Definición de un tablero adecuado para el problema
tab = Tablero(
    nro_filas=10,
    nro_columnas=10,
    celda_victoria=100,
    celdas_perdida=[16, 50, 80, 96],
    celdas_escalera=[(14, 46), (21, 77), (25, 36), (68, 90), (84, 100)],
    celdas_rodadero=[(44, 18), (73, 60), (93, 87)],
)
agente = AgenteQLearning(tab, epsilon=0.1, gamma=0.5)
run(tab, agente, episodios=100)


Episodio 1 terminó en 347 pasos, reward -1.0.
Episodio 2 terminó en 124 pasos, reward -1.0.
Episodio 3 terminó en 221 pasos, reward -1.0.
Episodio 4 terminó en 158 pasos, reward -1.0.
Episodio 5 terminó en 89 pasos, reward -1.0.
Episodio 6 terminó en 469 pasos, reward -1.0.
Episodio 7 terminó en 307 pasos, reward -1.0.
Episodio 8 terminó en 377 pasos, reward 1.0.
Episodio 9 terminó en 138 pasos, reward -1.0.
Episodio 10 terminó en 168 pasos, reward -1.0.
Episodio 11 terminó en 191 pasos, reward -1.0.
Episodio 12 terminó en 471 pasos, reward -1.0.
Episodio 13 terminó en 191 pasos, reward 1.0.
Episodio 14 terminó en 132 pasos, reward 1.0.
Episodio 15 terminó en 185 pasos, reward -1.0.
Episodio 16 terminó en 353 pasos, reward 1.0.
Episodio 17 terminó en 170 pasos, reward -1.0.
Episodio 18 terminó en 191 pasos, reward 1.0.
Episodio 19 terminó en 398 pasos, reward -1.0.
Episodio 20 terminó en 470 pasos, reward 1.0.
Episodio 21 terminó en 357 pasos, reward -1.0.
Episodio 22 terminó en 300 pa

<IPython.core.display.Javascript object>